In [72]:
import csv
import pandas as pd
import nltk
from nltk.tokenize import TweetTokenizer as tw_tokenizer
from unidecode import unidecode
import time

#Membaca file csv
datafile = r'data/kelompok1.csv'
data = pd.read_csv(datafile)

In [73]:
stopword_file1 = open('stopword/stopword_id.txt', "r").read() # Membuka file stopword bahasa indonesia dan menjadikan isi file tersebut sebagai string
stopword_file2 = open('stopword_en/stopwords_en.txt', "r").read()  # Membuka file stopword bahasa inggris dan menjadikan isi file tersebut sebagai string
stopword_file3 = open('stopword_noise/stopword_noise.txt', "r").read()  # Membuka file stopword noise dan menjadikan isi file tersebut sebagai string
stopword_file_all = stopword_file1 + stopword_file2 + stopword_file3  # Menggabungkan ketiga string stopword sebelumnya kedalam satu string
stopwords = stopword_file_all.split('\n') # Memisahkan kata dalam string yang sudah digambungkan berdasarkan baris
#print(stopwords)

In [74]:
slangwords = dict() # Membuat dictionary kosong untuk menyimpan kata slang dan formal sebagai key dan value
slangwords_dataframe = pd.read_csv('colloquial-indonesian-lexicon.csv') # Membuka file csv yang berisi kata slang dan formal dan mengkonversi kedalam dataframe
for slang, formal in zip(slangwords_dataframe['slang'], slangwords_dataframe['formal']):
    slangwords[slang] = formal # Mapping kata slang dan formal dan memasukkan ke dalam dictionary secara berulang

slangword_file = open('slangword/slangword.txt', "r").read() # Membuka file yang berisi kata slang dan kata formal dan mengkonversi kedalam string
slangwords_text = slangword_file.split('\n') # Memisahkan kata berdasarkan baris namun kata slang dan kata formal masih belum terpisah. output : (['slang:formal', ...])
#print(slangwords_text)
for slang in slangwords_text:
    split_slang = slang.split(":") # Memisahkan semua kata slang dan kata formal berdasarkan "titik dua (:)"
    slangwords[split_slang[0]] = split_slang[1] # Mapping semua kata slang dan kata formal ke dalam dictionary. Output : {'slang' : 'formal', ...}
#print(slangwords)

In [75]:
array_text = list(map(lambda tweet: unidecode(tweet).lower(), data['text'])) # Mapping semua text twitter dan memasukan ke dalam list. Output : ['teks panjang ...', 'teks panjang', ...]
long_text = ' '.join(array_text) # Menggabungkan semua text yang berada dalam list kedalam satu text
tokenized = tw_tokenizer().tokenize(long_text) # Memisahkan kata dalam text berasarkan "spasi"
filtered_alfanumeric = [w for w in tokenized if w.isalnum()] # Filtering kata yang hanya berisi karakater a-z dan 0-9 (Menghapus url, hashtag, mention)
#print(filtered_alfanumeric)

In [76]:
removed_stopwords = [w for w in filtered_alfanumeric if w not in stopwords] 
# Filtering data dengan menghapus kata yang tidak bermakna (Stopword yang diperoleh dari file)
#print(removed_stopwords)

In [77]:
handled_slangword = list(map(lambda w : slangwords[w] if w in slangwords.keys() else w, removed_stopwords))
# Mengubah kata slang menjadi kata formal (kata slang dan kata formal yang diperoleh dari dictionary) 
#print(handled_slangword)

In [79]:
start_time_sastrawi = time.time()
from Sastrawi.Stemmer.StemmerFactory import StemmerFactory # Import modul stemmer dari sastrawi

# create stemmer
factory = StemmerFactory() # Membuat factori untuk stemmer dengan memanggi objek StemmerFactory()
stemmer = factory.create_stemmer() # Membuat stemmer
# stemmed_by_sastrawi = [stemmer.stem(w) for w in handled_slangword] # Mengubah kata-kata menjadi kata dasar dengan menggunakan modul sastrawi
print(stemmer.stem("Melihat"))
end_time_sastrawi = time.time()

total_time_sastrawi = end_time_sastrawi - start_time_sastrawi

print("Hasil stem menggunakan modul Sastrawi adalah", total_time_sastrawi, "detik")

lihat
Hasil stem menggunakan modul Sastrawi adalah 0.24991798400878906 detik


In [81]:
start_time_spacy = time.time()
from spacy.lang.id import Indonesian # Import modul spacy bahasa indonesia

nlp = Indonesian() # memanggi objek Indonesian() pada modul spacy
def stem_spacy(text): # Fungsi untuk mengubah kata-kata menjadi kata dasar
    for txt in nlp(text):
        t = txt.lemma_
    return t
stemmed_by_spacy = [stem_spacy(w) for w in handled_slangword]  # Mengubah kata-kata menjadi kata dasar dengan menggunakan modul spacy
end_time_spacy = time.time()

total_time_spacy = end_time_spacy - start_time_spacy

print("Hasil stem menggunakan modul Spacy adalah", total_time_spacy, "detik\n") # Hasil running terakhir adalah 67.62633967399597 detik
print(stemmed_by_spacy)

Hasil stem menggunakan modul Spacy adalah 122.60337972640991 detik

['whahaha', 'benar', 'ledak', 'mercon', 'hancur', 'rumah', 'nanang', 'tewas', 'asih', 'bantu', 'kalideres', 'arah', 'batu', 'pendek', 'tangerang', 'tol', 'cawang', 'tmii', 'cibubur', 'bogor', 'ciawi', 'kesini', 'ku', 'tolong', 'manfaatin', 'honestly', 'indonesia', 'yang', 'rasa', 'beda', 'saya', 'cuaca', 'astagah', 'jam', 'keringeta', 'kang', 'bohong', 'bohongin', 'bagaimana', 'dikecewain', 'tetap', 'cinta', 'dasar', 'aku', 'hee', 'ingat', 'minggu', 'kemarin', 'tidak', 'sengaja', 'habis', 'injak', 'kocheng', 'allah', 'kochengnya', 'donnaruma', 'apa', 'sudah', 'diganti', 'tidak', 'balas', 'tidur', 'tidak', 'tidur', 'siang', 'tidur', 'siang', 'dibilang', 'tidur', 'mulu', 'tidak', 'tidur', 'siang', 'dikasianin', 'bucin', 'banget', 'tidak', 'opo', 'opo', 'iso', 'kecuali', 'siji', 'tangi', 'esuk', '1', 'tidak', 'dikasih', 'tidak', 'ngember', 'tidak', 'cerita', 'alesannya', 'simpl', 'tidak', 'baca', 'sepotong', 'berita', 'kr

In [71]:
" ".join(stemmed_by_spacy)

'whahaha benar ledak mercon hancur rumah nanang tewas asih bantu kalideres arah batu pendek tangerang tol cawang tmii cibubur bogor ciawi kesini ku tolong manfaatin honestly indonesia yang rasa beda saya cuaca astagah jam keringeta kang bohong bohongin bagaimana dikecewain tetap cinta dasar aku hee ingat minggu kemarin tidak sengaja habis injak kocheng allah kochengnya donnaruma apa sudah diganti tidak balas tidur tidak tidur siang tidur siang dibilang tidur mulu tidak tidur siang dikasianin bucin banget tidak opo opo iso kecuali siji tangi esuk 1 tidak dikasih tidak ngember tidak cerita alesannya simpl tidak baca sepotong berita kronologinya liput afc malam baca kal seakan atmosfir today ubah oaoe sweet menuaa tampung aspirasi warga butuh refresh butuh sejuk butuh hibur butuh tenang malas cari angkat tangan masak indomie 62 sudah beri negara 62 cuma kemarau penghujan jas hujan seru juga umbrella academy yaelah kemana corona untung besar fast furious kemarin serly selingkuh teman suami

In [ ]:
databersih = pd.dataframe()
